In [1]:
# Imports
import pandas as pd
import numpy as np
from sklearn import preprocessing
from sklearn.model_selection import train_test_split
from sklearn.ensemble import RandomForestRegressor, GradientBoostingRegressor
from sklearn.metrics import mean_squared_error
from xgboost import XGBRegressor
import optuna

In [2]:
# Model 1
df = pd.read_csv("data/train_folds.csv")
df_test = pd.read_csv("data/test.csv")
sample_submission = pd.read_csv("data/sample_submission.csv")

useful_features = [c for c in df.columns if c not in ("id", "target", "kfold")]
object_cols = [col for col in useful_features if 'cat' in col]
numerical_cols = [col for col in useful_features if col.startswith("cont")]
df_test = df_test[useful_features]

for col in numerical_cols:
    df[col] = np.log1p(df[col])
    df_test[col] = np.log1p(df_test[col])

useful_features = [c for c in df.columns if c not in ("id", "target", "kfold")]
object_cols = [col for col in useful_features if 'cat' in col]
df_test = df_test[useful_features]


In [2]:
def run(trial):
    fold = 0
    learning_rate = trial.suggest_float("learning_rate", 1e-2, 0.25, log=True)
    reg_lambda = trial.suggest_loguniform("reg_lambda", 1e-8, 100.0)
    reg_alpha = trial.suggest_loguniform("reg_alpha", 1e-8, 100.0)
    subsample = trial.suggest_float("subsample", 0.1, 1.0)
    colsample_bytree = trial.suggest_float("colsample_bytree", 0.1, 1.0)
    max_depth = trial.suggest_int("max_depth", 1, 7)

    xtrain = df[df.kfold != fold].reset_index(drop=True)
    xvalid = df[df.kfold == fold].reset_index(drop=True)

    ytrain = xtrain.target
    yvalid = xvalid.target

    xtrain = xtrain[useful_features]
    xvalid = xvalid[useful_features]

    ordinal_encoder = preprocessing.OrdinalEncoder()
    xtrain[object_cols] = ordinal_encoder.fit_transform(xtrain[object_cols])
    xvalid[object_cols] = ordinal_encoder.transform(xvalid[object_cols])

    model = XGBRegressor(
        random_state=42,
        tree_method='gpu_hist',
        gpu_id=1,
        predictor="gpu_predictor",
        n_estimators=7000,
        learning_rate=learning_rate,
        reg_lambda=reg_lambda,
        reg_alpha=reg_alpha,
        subsample=subsample,
        colsample_bytree=colsample_bytree,
        max_depth=max_depth,
    )
    model.fit(xtrain, ytrain, early_stopping_rounds=300, eval_set=[(xvalid, yvalid)], verbose=1000)
    preds_valid = model.predict(xvalid)
    rmse = mean_squared_error(yvalid, preds_valid, squared=False)
    return rmse

In [4]:
study = optuna.create_study(direction="minimize")
study.optimize(run, n_trials=100) #100

[I 2021-08-29 17:16:26,798] A new study created in memory with name: no-name-7dd346c2-e927-4a92-9cdf-0b59ce19e471


[17:16:29] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.4.0/src/learner.cc:231: Only 1 GPUs are visible, setting `gpu_id` to 0
[0]	validation_0-rmse:7.64445
[1000]	validation_0-rmse:0.72663
[2000]	validation_0-rmse:0.72255
[3000]	validation_0-rmse:0.72050
[4000]	validation_0-rmse:0.71928
[5000]	validation_0-rmse:0.71856
[6000]	validation_0-rmse:0.71809
[6999]	validation_0-rmse:0.71783


[I 2021-08-29 17:17:28,191] Trial 0 finished with value: 0.7178241183314773 and parameters: {'learning_rate': 0.01756937523162302, 'reg_lambda': 1.0853151506759414e-07, 'reg_alpha': 2.5160929834612467, 'subsample': 0.6362270243609827, 'colsample_bytree': 0.3333421958988413, 'max_depth': 3}. Best is trial 0 with value: 0.7178241183314773.


[17:17:29] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.4.0/src/learner.cc:231: Only 1 GPUs are visible, setting `gpu_id` to 0
[0]	validation_0-rmse:7.68761
[1000]	validation_0-rmse:0.72182
[2000]	validation_0-rmse:0.71971
[3000]	validation_0-rmse:0.71926
[3539]	validation_0-rmse:0.71927


[I 2021-08-29 17:18:54,935] Trial 1 finished with value: 0.719203740606503 and parameters: {'learning_rate': 0.011969126061443562, 'reg_lambda': 0.00908222386310185, 'reg_alpha': 0.25781199761018764, 'subsample': 0.9290904339770187, 'colsample_bytree': 0.4779906301858352, 'max_depth': 7}. Best is trial 0 with value: 0.7178241183314773.


...

[I 2021-08-29 18:45:02,975] Trial 97 finished with value: 0.71708954303124 and parameters: {'learning_rate': 0.024439210487440542, 'reg_lambda': 18.77100771245707, 'reg_alpha': 2.670030252295931, 'subsample': 0.6977154819880925, 'colsample_bytree': 0.1380321161124814, 'max_depth': 4}. Best is trial 51 with value: 0.7169064837392827.


[18:45:04] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.4.0/src/learner.cc:231: Only 1 GPUs are visible, setting `gpu_id` to 0
[0]	validation_0-rmse:7.62123
[1000]	validation_0-rmse:0.72310
[2000]	validation_0-rmse:0.71955
[3000]	validation_0-rmse:0.71824
[4000]	validation_0-rmse:0.71763
[5000]	validation_0-rmse:0.71738
[5261]	validation_0-rmse:0.71740


[I 2021-08-29 18:45:54,847] Trial 98 finished with value: 0.7173808135080316 and parameters: {'learning_rate': 0.020587555581724565, 'reg_lambda': 6.623262643487766, 'reg_alpha': 4.2072925946675664e-05, 'subsample': 0.5481507083493457, 'colsample_bytree': 0.2029470107251543, 'max_depth': 4}. Best is trial 51 with value: 0.7169064837392827.


[18:45:56] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.4.0/src/learner.cc:231: Only 1 GPUs are visible, setting `gpu_id` to 0
[0]	validation_0-rmse:7.56913
[1000]	validation_0-rmse:0.72333
[2000]	validation_0-rmse:0.72008
[3000]	validation_0-rmse:0.71898
[4000]	validation_0-rmse:0.71856
[5000]	validation_0-rmse:0.71839
[5822]	validation_0-rmse:0.71836


[I 2021-08-29 18:47:04,368] Trial 99 finished with value: 0.7183400930175847 and parameters: {'learning_rate': 0.027361891720247507, 'reg_lambda': 80.24704110944548, 'reg_alpha': 63.679263739724455, 'subsample': 0.7188690417044336, 'colsample_bytree': 0.5024822510206274, 'max_depth': 4}. Best is trial 51 with value: 0.7169064837392827.


In [5]:
study.best_params

{'learning_rate': 0.0342032910688893,
 'reg_lambda': 16.984336234349644,
 'reg_alpha': 13.2209270507238,
 'subsample': 0.7396101488182523,
 'colsample_bytree': 0.13653907086890005,
 'max_depth': 3}

In [7]:
# Model 2
df = pd.read_csv("data/train_folds.csv")
df_test = pd.read_csv("data/test.csv")
sample_submission = pd.read_csv("data/sample_submission.csv")

useful_features = [c for c in df.columns if c not in ("id", "target", "kfold")]
object_cols = [col for col in useful_features if 'cat' in col]
df_test = df_test[useful_features]

study = optuna.create_study(direction="minimize")
study.optimize(run, n_trials=100) #100

[I 2021-08-29 18:47:44,719] A new study created in memory with name: no-name-7acf527b-9e92-426f-8318-4ce3028973d7


[18:47:45] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.4.0/src/learner.cc:231: Only 1 GPUs are visible, setting `gpu_id` to 0
[0]	validation_0-rmse:7.63239
[1000]	validation_0-rmse:0.72154
[2000]	validation_0-rmse:0.72028
[2305]	validation_0-rmse:0.72037


[I 2021-08-29 18:48:21,683] Trial 0 finished with value: 0.7202673872752845 and parameters: {'learning_rate': 0.0191379813907593, 'reg_lambda': 1.4363127879918497e-08, 'reg_alpha': 0.00041415689595605197, 'subsample': 0.4170488901687981, 'colsample_bytree': 0.8690280656001025, 'max_depth': 6}. Best is trial 0 with value: 0.7202673872752845.


[18:48:22] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.4.0/src/learner.cc:231: Only 1 GPUs are visible, setting `gpu_id` to 0
[0]	validation_0-rmse:7.36516
[1000]	validation_0-rmse:0.71982
[1951]	validation_0-rmse:0.71943


[I 2021-08-29 18:48:48,109] Trial 1 finished with value: 0.7193494439165233 and parameters: {'learning_rate': 0.05384256063858188, 'reg_lambda': 8.776323950846218e-07, 'reg_alpha': 48.421734302412716, 'subsample': 0.5053790749130518, 'colsample_bytree': 0.8462785533989301, 'max_depth': 5}. Best is trial 1 with value: 0.7193494439165233.


...

[I 2021-08-29 20:30:40,155] Trial 97 finished with value: 0.7173690207110963 and parameters: {'learning_rate': 0.018673727237094442, 'reg_lambda': 5.33214670254417, 'reg_alpha': 3.692281276550072, 'subsample': 0.646854725143019, 'colsample_bytree': 0.14328177227517755, 'max_depth': 6}. Best is trial 73 with value: 0.7169119261340184.


[20:30:41] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.4.0/src/learner.cc:231: Only 1 GPUs are visible, setting `gpu_id` to 0
[0]	validation_0-rmse:7.69334
[1000]	validation_0-rmse:0.72787
[2000]	validation_0-rmse:0.72107
[3000]	validation_0-rmse:0.71868
[4000]	validation_0-rmse:0.71778
[5000]	validation_0-rmse:0.71737
[6000]	validation_0-rmse:0.71719
[6999]	validation_0-rmse:0.71712


[I 2021-08-29 20:32:28,964] Trial 98 finished with value: 0.7171147064675906 and parameters: {'learning_rate': 0.011228487579705387, 'reg_lambda': 12.360183215832858, 'reg_alpha': 10.554912050577249, 'subsample': 0.7964916478773698, 'colsample_bytree': 0.11772466556467015, 'max_depth': 6}. Best is trial 73 with value: 0.7169119261340184.


[20:32:30] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.4.0/src/learner.cc:231: Only 1 GPUs are visible, setting `gpu_id` to 0
[0]	validation_0-rmse:7.69265
[1000]	validation_0-rmse:0.72453
[2000]	validation_0-rmse:0.71982
[3000]	validation_0-rmse:0.71831
[4000]	validation_0-rmse:0.71762
[5000]	validation_0-rmse:0.71730
[6000]	validation_0-rmse:0.71721
[6141]	validation_0-rmse:0.71723


[I 2021-08-29 20:34:11,483] Trial 99 finished with value: 0.7172095737207993 and parameters: {'learning_rate': 0.011317078535432935, 'reg_lambda': 10.046690254077859, 'reg_alpha': 11.950519329184143, 'subsample': 0.8080841261613334, 'colsample_bytree': 0.19953454892298766, 'max_depth': 6}. Best is trial 73 with value: 0.7169119261340184.


In [8]:
study.best_params

{'learning_rate': 0.015603699193600313,
 'reg_lambda': 0.001158068570366239,
 'reg_alpha': 16.448429406371936,
 'subsample': 0.5948693703077814,
 'colsample_bytree': 0.12425047105688761,
 'max_depth': 5}

# Model 3 Test

In [8]:
df = pd.read_csv("data/train_folds.csv")
df_test = pd.read_csv("data/test.csv")
sample_submission = pd.read_csv("data/sample_submission.csv")

df1 = pd.read_csv("train_pred_1.csv")
df1.columns = ["id", "pred_1"]
df2 = pd.read_csv("train_pred_2.csv")
df2.columns = ["id", "pred_2"]
df3 = pd.read_csv("train_pred_3.csv")


df_test1 = pd.read_csv("test_pred_1.csv")
df_test1.columns = ["id", "pred_1"]
df_test2 = pd.read_csv("test_pred_2.csv")
df_test2.columns = ["id", "pred_2"]
df_test3 = pd.read_csv("test_pred_3.csv")


df = df.merge(df1, on="id", how="left")
df = df.merge(df2, on="id", how="left")


df_test = df_test.merge(df_test1, on="id", how="left")
df_test = df_test.merge(df_test2, on="id", how="left")


In [9]:
def run(trial):
    fold = 0
    learning_rate = trial.suggest_float("learning_rate", 1e-2, 0.25, log=True)
    reg_lambda = trial.suggest_loguniform("reg_lambda", 1e-8, 100.0)
    reg_alpha = trial.suggest_loguniform("reg_alpha", 1e-8, 100.0)
    subsample = trial.suggest_float("subsample", 0.1, 1.0)
    colsample_bytree = trial.suggest_float("colsample_bytree", 0.1, 1.0)
    max_depth = trial.suggest_int("max_depth", 1, 7)

    xtrain = df[df.kfold != fold].reset_index(drop=True)
    xvalid = df[df.kfold == fold].reset_index(drop=True)

    ytrain = xtrain.target
    yvalid = xvalid.target

    xtrain = xtrain[useful_features]
    xvalid = xvalid[useful_features]

    model = XGBRegressor(
        random_state=42,
        tree_method='gpu_hist',
        gpu_id=1,
        predictor="gpu_predictor",
        n_estimators=7000,
        learning_rate=learning_rate,
        reg_lambda=reg_lambda,
        reg_alpha=reg_alpha,
        subsample=subsample,
        colsample_bytree=colsample_bytree,
        max_depth=max_depth,
    )
    model.fit(xtrain, ytrain, early_stopping_rounds=300, eval_set=[(xvalid, yvalid)], verbose=1000)
    preds_valid = model.predict(xvalid)
    rmse = mean_squared_error(yvalid, preds_valid, squared=False)
    return rmse

In [12]:
useful_features = ["pred_1", "pred_2"]
df_test = df_test[useful_features]

study = optuna.create_study(direction="minimize")
study.optimize(run, n_trials=5000) #100

[I 2021-08-30 18:10:04,457] A new study created in memory with name: no-name-af5ae157-76de-4869-aded-4f1243ec5e24


[18:10:04] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.4.0/src/learner.cc:231: Only 1 GPUs are visible, setting `gpu_id` to 0
[0]	validation_0-rmse:7.51657
[561]	validation_0-rmse:0.71723


[I 2021-08-30 18:10:06,769] Trial 0 finished with value: 0.7171551714586599 and parameters: {'learning_rate': 0.034174761769190355, 'reg_lambda': 25.70771354978567, 'reg_alpha': 2.2296106178141343e-08, 'subsample': 0.5362824716354035, 'colsample_bytree': 0.20683590259834822, 'max_depth': 4}. Best is trial 0 with value: 0.7171551714586599.


[18:10:06] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.4.0/src/learner.cc:231: Only 1 GPUs are visible, setting `gpu_id` to 0
[0]	validation_0-rmse:7.43439
[509]	validation_0-rmse:0.71720


[I 2021-08-30 18:10:08,663] Trial 1 finished with value: 0.7171609778403893 and parameters: {'learning_rate': 0.044809087819172415, 'reg_lambda': 0.0014358459806968846, 'reg_alpha': 5.683406927505941e-05, 'subsample': 0.8238463501862088, 'colsample_bytree': 0.2742609526274012, 'max_depth': 3}. Best is trial 0 with value: 0.7171551714586599.


...

[I 2021-08-30 21:45:43,159] Trial 4997 finished with value: 0.7171742643034629 and parameters: {'learning_rate': 0.1442900412701705, 'reg_lambda': 16.252033900802957, 'reg_alpha': 1.9665588341221751, 'subsample': 0.1161067075197632, 'colsample_bytree': 0.5704353639976792, 'max_depth': 1}. Best is trial 4951 with value: 0.7170176939897599.


[21:45:43] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.4.0/src/learner.cc:231: Only 1 GPUs are visible, setting `gpu_id` to 0
[0]	validation_0-rmse:6.87971
[438]	validation_0-rmse:0.71712


[I 2021-08-30 21:45:44,655] Trial 4998 finished with value: 0.7170778414087042 and parameters: {'learning_rate': 0.11685191816037294, 'reg_lambda': 2.357895105266745e-05, 'reg_alpha': 1.000859985048868, 'subsample': 0.14229891866364547, 'colsample_bytree': 0.5559002574575996, 'max_depth': 1}. Best is trial 4951 with value: 0.7170176939897599.


[21:45:45] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.4.0/src/learner.cc:231: Only 1 GPUs are visible, setting `gpu_id` to 0
[0]	validation_0-rmse:6.71695
[417]	validation_0-rmse:0.71715


[I 2021-08-30 21:45:46,128] Trial 4999 finished with value: 0.7171059197411125 and parameters: {'learning_rate': 0.13807296927402152, 'reg_lambda': 6.5841713897622975, 'reg_alpha': 2.957922723293696, 'subsample': 0.12008934024161186, 'colsample_bytree': 0.5719886551649463, 'max_depth': 1}. Best is trial 4951 with value: 0.7170176939897599.


In [13]:
study.best_params

{'learning_rate': 0.12289452566887417,
 'reg_lambda': 6.648194058133428,
 'reg_alpha': 0.33939128068787006,
 'subsample': 0.10017240258093753,
 'colsample_bytree': 0.792182676498984,
 'max_depth': 1}